In [6]:
import pandas as pd
import numpy as np
import re
import requests
import plotly
import html
import time

from bs4 import BeautifulSoup

In [7]:
url = 'https://twitter.com/thejakartaglobe?ref_src=twsrc%5Egoogle%7Ctwcamp%5Eserp%7Ctwgr%5Eauthor'

res = requests.get(url)
soup = BeautifulSoup(res.content, 'lxml')

In [8]:
import time
from selenium import webdriver
from bs4 import BeautifulSoup as bs

# I used Firefox; you can use whichever browser you like.
browser = webdriver.Chrome()

# Tell Selenium to get the URL you're interested in.
browser.get("https://twitter.com/thejakartaglobe?lang=en")

# Selenium script to scroll to the bottom, wait 3 seconds for the next batch of data to load, then continue scrolling.  It will continue to do this until the page stops loading new data.
lenOfPage = browser.execute_script("window.scrollTo(0, document.body.scrollHeight);var lenOfPage=document.body.scrollHeight;return lenOfPage;")
match=False
while(match==False):
        lastCount = lenOfPage
        time.sleep(1)
        lenOfPage = browser.execute_script("window.scrollTo(0, document.body.scrollHeight);var lenOfPage=document.body.scrollHeight;return lenOfPage;")
        if lastCount==lenOfPage:
            match=True

# Now that the page is fully scrolled, grab the source code.
source_data = browser.page_source

# Throw your source into BeautifulSoup and start parsing!
bs_data = bs(source_data)

/anaconda3/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning:

No parser was explicitly specified, so I'm using the best available HTML parser for this system ("lxml"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /anaconda3/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "lxml")




In [9]:
bs_data

<!DOCTYPE html>
<html data-scribe-reduced-action-queue="true" lang="en" xmlns="http://www.w3.org/1999/xhtml"><head>
<meta charset="utf-8"/>
<script async="" src="//www.google-analytics.com/analytics.js"></script><script nonce="">
        !function(){window.initErrorstack||(window.initErrorstack=[]),window.onerror=function(r,i,n,o,t){r.indexOf("Script error.")&gt;-1||window.initErrorstack.push({errorMsg:r,url:i,lineNumber:n,column:o,errorObj:t})}}();
      </script>
<script id="bouncer_terminate_iframe" nonce="">
    if (window.top != window) {
  window.top.postMessage({'bouncer': true, 'event': 'complete'}, '*');
}
  </script>
<script id="ttft_boot_data" nonce="">
    window.ttftData={"transaction_id":"004e593900ab6536.b34e5d73e9abd49f\u003c:00224a100097486d","server_request_start_time":1547389695626,"user_id":null,"is_ssl":true,"rendered_on_server":true,"is_tfe":true,"client":"macaw-swift","tfe_version":"tsa_b\/1.0.1\/20181203.1934.172fbb5","ttft_browser":"chrome"};!function(){functio

In [70]:
str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[0]).split('href="/')[1].split('/status')[0]

'thejakartaglobe'

---

## Number of Tweets Captured

In [131]:
num_tweets = len(list(bs_data.find_all('p', {'class': 'TweetTextSize TweetTextSize--normal js-tweet-text tweet-text'})))

---

## Handle

In [75]:
str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[0]).split('href="/')[1].split('/status')[0]

'thejakartaglobe'

---

## Time

In [80]:
time_str = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[0]).split('title="')[1].split('"><span ')[0].split(' - ')[0]

---

## Date

Day

In [81]:
day_str = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[0]).split('title="')[1].split('"><span ')[0].split('-')[1].lstrip().split(' ')[0]

Month

In [82]:
month_str = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[0]).split('title="')[1].split('"><span ')[0].split('-')[1].lstrip().split(' ')[1]

Year

In [83]:
year_str = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[0]).split('title="')[1].split('"><span ')[0].split('-')[1].lstrip().split(' ')[2]

---

## Convert to datetime object

In [84]:
from datetime import datetime

#datetime_object = datetime.strptime('Jun 1 2005  1:33PM', '%b %d %Y %I:%M%p')

In [88]:
time_str.replace(" ", "")

'6:25AM'

In [89]:
datetime_object = datetime.strptime(month_str + ' ' + day_str + ' ' + year_str + ' ' + time_str.replace(" ", ""), '%b %d %Y %I:%M%p')

---

## Tweet

In [101]:
tweet = str(list(bs_data.find_all('p', {'class': 'TweetTextSize TweetTextSize--normal js-tweet-text tweet-text'}))[0]).split('lang="en">')[1].split('<a class')[0].rstrip()

---

## Check for keyword (tsunami)

In [103]:
tweet = 'This is a tweet about a tsunami'

In [104]:
'tsunami' in tweet

True

---

## Build Dictionary

In [119]:
temp_dict = {}

temp_dict['handle']     = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[0]).split('href="/')[1].split('/status')[0]
temp_dict['tweet']      = str(list(bs_data.find_all('p', {'class': 'TweetTextSize TweetTextSize--normal js-tweet-text tweet-text'}))[0]).split('lang="en">')[1].split('<a class')[0].rstrip()
temp_dict['datetime']   = datetime_object
temp_dict['if_tsunami'] = 'tsunami' in temp_dict['tweet']

In [125]:
temp_dict

{'handle': 'thejakartaglobe',
 'tweet': 'China Pledges Easier Foreign Tourist Access to Tibet Amid US Pressure',
 'datetime': datetime.datetime(2019, 1, 13, 6, 25),
 'if_tsunami': False}

In [172]:
master_list = []
loop_range = num_tweets - 1

for i in range(loop_range):
    temp_dict = {}

    temp_dict['handle']     = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[i]).split('href="/')[1].split('/status')[0]
    
    try:
        temp_dict['tweet']      = str(list(bs_data.find_all('p', {'class': 'TweetTextSize TweetTextSize--normal js-tweet-text tweet-text'}))[i]).split('lang="en">')[1].split('<a class')[0].rstrip()
    except IndexError:
        temp_dict['tweet']      = ""
    
    temp_dict['day']        = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[i]).split('title="')[1].split('"><span ')[0].split('-')[1].lstrip().split(' ')[0]
    temp_dict['month']      = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[i]).split('title="')[1].split('"><span ')[0].split('-')[1].lstrip().split(' ')[1]
    temp_dict['year']       = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[i]).split('title="')[1].split('"><span ')[0].split('-')[1].lstrip().split(' ')[2]
    temp_dict['time']       = str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[i]).split('title="')[1].split('"><span ')[0].split(' - ')[0]
    
    datetime_object = datetime.strptime(temp_dict['month'] + ' ' + temp_dict['day'] + ' ' + temp_dict['year'] + ' ' + temp_dict['time'].replace(" ", ""), '%b %d %Y %I:%M%p')
    
    temp_dict['datetime']   = datetime_object
    temp_dict['if_tsunami'] = 'tsunami' in temp_dict['tweet'] or 'Tsunami' in tweet
    
    master_list.append(temp_dict)
    

In [174]:
pd.DataFrame(master_list).to_csv('thejakartaglobe_tweetscrape.csv', sep=",", index=False)

In [175]:
tweet = 'this is a tweet with Tsunami in it'

In [176]:
'tsunami' in tweet or 'Tsunami' in tweet

True

In [149]:
range(loop_range)

range(0, 579)

In [153]:
str(list(bs_data.find_all('a', {'class': 'tweet-timestamp js-permalink js-nav js-tooltip'}))[579]).split('href="/')[1].split('/status')[0]

'thejakartaglobe'

In [155]:
i

5

In [ ]:
str(list(bs_data.find_all('p', {'class': 'TweetTextSize TweetTextSize--normal js-tweet-text tweet-text'}))[5]).split('lang="en">')[1].split('<a class')[0].rstrip()